# Skolemization

## Example 1: "Ringo"

Example taken from 
https://github.com/RDFLib/rdflib/issues/1404

In [1]:
from rdflib import Graph


ttl = '''
@prefix wd: <http://www.wikidata.org/entity/> .
@prefix foaf: <http://xmlns.com/foaf/0.1/> .

wd:Q1203 foaf:knows [ a foaf:Person;
    foaf:name "Ringo" ].
    

'''

graph = Graph()
graph.parse(data=ttl, format='turtle')
skolemized = graph.skolemize()
skolemized.namespace_manager.bind('foaf', 'http://xmlns.com/foaf/0.1/')
print(skolemized.serialize(format='turtle'))

@prefix foaf: <http://xmlns.com/foaf/0.1/> .

<http://www.wikidata.org/entity/Q1203> foaf:knows <https://rdflib.github.io/.well-known/genid/rdflib/n7dfd882820d54ad28b8173ea7f083f31b1> .

<https://rdflib.github.io/.well-known/genid/rdflib/n7dfd882820d54ad28b8173ea7f083f31b1> a foaf:Person ;
    foaf:name "Ringo" .




In [2]:
deskolemized = skolemized.de_skolemize()
deskolemized.namespace_manager.bind('foaf', 'http://xmlns.com/foaf/0.1/')
print(deskolemized.serialize(format='turtle'))

@prefix foaf: <http://xmlns.com/foaf/0.1/> .

<http://www.wikidata.org/entity/Q1203> foaf:knows [ a foaf:Person ;
            foaf:name "Ringo" ] .




## Example 2: Husband

In [3]:
infer = True
skolem = False

In [4]:
from rdflib import Graph
import owlrl

In [5]:
ttl = """
@prefix : <http://example.com/ns#> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .


# T-Box

:Person a owl:Class .

:Husband
    a owl:Class ;
    owl:equivalentClass 
        [ a owl:Restriction ;
          owl:onProperty :has_partner ;
          owl:someValuesFrom :Person ] .

:has_partner a owl:ObjectProperty .


# A-Box

:Eve a :Person .
:Helen a :Person.

# Adam is a husband with a known partner 
:Adam
    a :Husband ;
    :has_partner :Eve .

# Hans is a person, who has a known partner.
# The inferencing system should classify him
# beeing a husband. 
:Hans
    a :Person ;
    :has_partner :Helen .

# Hugo is a husband. Thus he has a partner. 
# But we do not know the partner.
# Q: Does the inferencing system allocate a blank node automativally?
# A: no! 

:Hugo
    a :Husband .
"""



In [6]:
graph = Graph()
graph.parse(data = ttl, format='ttl')
print(f"#triples: {len(graph)}")

#triples: 14


In [7]:
if infer:
    owlrl.DeductiveClosure(owlrl.OWLRL_Semantics,
        axiomatic_triples = False).expand(graph)
print(f"infer: {infer}, #triples: {len(graph)}")

infer: True, #triples: 161


In [8]:
skolemized = graph.skolemize() if skolem else graph

skolemized.namespace_manager.bind('', 'http://example.com/ns#')
skolemized.namespace_manager.bind('owl', 'http://www.w3.org/2002/07/owl#')

print("skolem:", skolem, "\n\n", skolemized.serialize(format='turtle'))


skolem: False 

 @prefix : <http://example.com/ns#> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .

:Adam a _:n9777f20140ce4b41ac4ccd4bcf792416b1,
        :Husband,
        owl:Thing ;
    :has_partner :Eve ;
    owl:sameAs :Adam .

:Hans a _:n9777f20140ce4b41ac4ccd4bcf792416b1,
        :Husband,
        :Person,
        owl:Thing ;
    :has_partner :Helen ;
    owl:sameAs :Hans .

:Hugo a _:n9777f20140ce4b41ac4ccd4bcf792416b1,
        :Husband,
        owl:Thing ;
    owl:sameAs :Hugo .

rdf:HTML a rdfs:Datatype ;
    owl:sameAs rdf:HTML .

rdf:PlainLiteral a rdfs:Datatype ;
    owl:sameAs rdf:PlainLiteral .

rdf:XMLLiteral a rdfs:Datatype ;
    owl:sameAs rdf:XMLLiteral .

rdf:langString a rdfs:Datatype ;
    owl:sameAs rdf:langString .

rdf:type owl:sameAs rdf:type .

rdfs:Literal a rdfs:Datatype ;
    owl:sameAs r

In [9]:
Q = """
PREFIX : <http://example.com/ns#> 
PREFIX owl: <http://www.w3.org/2002/07/owl#> 
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
PREFIX xsd: <http://www.w3.org/2001/XMLSchema#> 

SELECT ?type ?a ?b 
WHERE
  { ?a 
      a ?type;
      :has_partner ?b .}
"""

qres = skolemized.query(Q)
for p,q,r in qres:
    print(p,q,r)

http://example.com/ns#Husband http://example.com/ns#Adam http://example.com/ns#Eve
n9777f20140ce4b41ac4ccd4bcf792416b1 http://example.com/ns#Adam http://example.com/ns#Eve
http://www.w3.org/2002/07/owl#Thing http://example.com/ns#Adam http://example.com/ns#Eve
http://example.com/ns#Person http://example.com/ns#Hans http://example.com/ns#Helen
n9777f20140ce4b41ac4ccd4bcf792416b1 http://example.com/ns#Hans http://example.com/ns#Helen
http://www.w3.org/2002/07/owl#Thing http://example.com/ns#Hans http://example.com/ns#Helen
http://example.com/ns#Husband http://example.com/ns#Hans http://example.com/ns#Helen
